In [ ]:
!pip install -qU networkx python-louvain tensorflow-gnn

     ━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━ 1.0/1.0 MB 11.4 MB/s eta 0:00:00


In [ ]:
import networkx as nx
import community
import pandas as pd
import numpy as np
import matplotlib.pyplot as plt
import seaborn as sns
import torch
import torch.nn as nn
import torch.nn.functional as F
from torch_geometric.data import Data, DataLoader
from torch_geometric.nn import GCNConv
from sklearn.model_selection import train_test_split

In [ ]:
pd.set_option('display.max_columns', None)

**Data Exploration and Preparation:**

In [ ]:
file_path = '/content/drive/MyDrive/dataset.csv'

In [ ]:
mts_data = pd.read_csv(file_path, index_col='Time')

In [ ]:
mts_data

[1:0]  [1:1]  [1:2]  [1:3]  [1:4]         [1:5]  \
Time                                                                       
2023-11-12 07:58:28.430  24121 -10137 -14957 -11379    0.0  0.000000e+00   
2023-11-12 07:58:29.430  24121 -10137 -14957 -11379    0.0  0.000000e+00   
2023-11-12 07:58:30.430  24121 -10137 -14957 -11379    0.0  2.350990e-38   
2023-11-12 07:58:31.430  24121 -10137 -14957 -11379    0.0  0.000000e+00   
2023-11-12 07:58:32.430  24121 -10137 -14957 -11379    0.0  0.000000e+00   
...                        ...    ...    ...    ...    ...           ...   
2023-11-12 09:58:23.460  11894 -22435 -27227 -23672    0.0  0.000000e+00   
2023-11-12 09:58:24.460  11894 -22435 -27227 -23672    0.0  0.000000e+00   
2023-11-12 09:58:25.460  11894 -22435 -27227 -23672    0.0  0.000000e+00   
2023-11-12 09:58:26.460  11894 -22435 -27227 -23672    0.0           NaN   
2023-11-12 09:58:27.460  11894 -22435 -27227 -23672    0.0  0.000000e+00   

                         [1:6]  [1:7]  [1:8]  [1:9]  [1:10]  [1:11]  [1:12]  \
Time                                                                          
2023-11-12 07:58:28.430      0    330    330    332     332     900      90   
2023-11-12 07:58:29.430      0    330    330    332     332     900      90   
2023-11-12 07:58:30.430      1    330    330    332     332     900      90   
2023-11-12 07:58:31.430      0    330    330    332     332     900      90   
2023-11-12 07:58:32.430      0    330    330    332     332     900      90   
...                        ...    ...    ...    ...     ...     ...     ...   
2023-11-12 09:58:23.460      0     18     18     18      18    -900     -89   
2023-11-12 09:58:24.460      0     18     18     18      18    -900     -89   
2023-11-12 09:58:25.460      0     18     18     18      18    -900     -89   
2023-11-12 09:58:26.460     -1     18     18     18      18    -900     -89   
2023-11-12 09:58:27.460      0     18     18     18      18    -900     -89   

                         [1:13]  [1:14]  [1:15]  [1:16]  [1:17]  [1:18]  \
Time                                                                      
2023-11-12 07:58:28.430       0       0       0    1000       0       0   
2023-11-12 07:58:29.430       0       0       0    1000       0       0   
2023-11-12 07:58:30.430       0       0       0    1000       0       0   
2023-11-12 07:58:31.430       0       0       0    1000       0       0   
2023-11-12 07:58:32.430       0       0       0    1000       0       0   
...                         ...     ...     ...     ...     ...     ...   
2023-11-12 09:58:23.460       0       0       0    1000       0       0   
2023-11-12 09:58:24.460       0       0       0    1000       0       0   
2023-11-12 09:58:25.460       0       0       0    1000       0       0   
2023-11-12 09:58:26.460       0       0       0    1000       0       0   
2023-11-12 09:58:27.460       0       0       0    1000       0       0   

                         [1:19]  [1:20]  [1:21]  [1:22]  [1:23]  [1:24]  \
Time                                                                      
2023-11-12 07:58:28.430       0    1000     194       0       0       0   
2023-11-12 07:58:29.430       0    1000     194       0       0       0   
2023-11-12 07:58:30.430       0    1000     194       0       0       0   
2023-11-12 07:58:31.430       0    1000     194       0       0       0   
2023-11-12 07:58:32.430       0    1000     194       0       0       0   
...                         ...     ...     ...     ...     ...     ...   
2023-11-12 09:58:23.460       0    1000     125       0       0       0   
2023-11-12 09:58:24.460       0    1000     125       0       0       0   
2023-11-12 09:58:25.460       0    1000     125       0       0       0   
2023-11-12 09:58:26.460       0    1000     125       0       0       0   
2023-11-12 09:58:27.460       0    1000     125       0       0       0   

                         [1:25]  [1:26]  [1:27]  [1:28] 

In [ ]:
mts_data.columns

Index(['[1:0]', '[1:1]', '[1:2]', '[1:3]', '[1:4]', '[1:5]', '[1:6]', '[1:7]',
       '[1:8]', '[1:9]',
       ...
       '[26.114]', '[26.115]', '[26.116]', '[26.117]', '[26.118]', '[26.119]',
       '[26.120]', '[26.121]', '[26.122]', '[26.123]'],
      dtype='object', length=2623)

In [ ]:
print(mts_data.head(0))

Empty DataFrame
Columns: [[1:0], [1:1], [1:2], [1:3], [1:4], [1:5], [1:6], [1:7], [1:8], [1:9], [1:10], [1:11], [1:12], [1:13], [1:14], [1:15], [1:16], [1:17], [1:18], [1:19], [1:20], [1:21], [1:22], [1:23], [1:24], [1:25], [1:26], [1:27], [1:28], [1:29], [1:30], [1:31], [1:32], [1:33], [1:34], [1:35], [1:36], [1:37], [1:38], [1:39], [1:40], [1:41], [1:42], [1:43], [1:44], [1:45], [1:46], [1:47], [1:48], [1:49], [1:50], [1:51], [1:52], [1:53], [1:54], [1:55], [1:56], [1:59], [1:60], [1:61], [1:62], [1:63], [1:64], [1:65], [1:66], [1:67], [1:68], [1:69], [1:70], [1:71], [1:72], [1:73], [1:74], [1:75], [1:76], [1:77], [1:78], [1:79], [1:80], [1:81], [1.0], [1.1], [1.2], [1.3], [1.4], [1.5], [1.6], [1.7], [1.8], [1.9], [1.10], [1.11], [1.12], [1.13], [1.14], [1.15], [1.16], [1.17], [1.18], [1.19], ...]
Index: []


In [ ]:
print(mts_data.info())

<class 'pandas.core.frame.DataFrame'>
Index: 7200 entries, 2023-11-12 07:58:28.430 to 2023-11-12 09:58:27.460
Columns: 2623 entries, [1:0] to [26.123]
dtypes: float64(299), int64(2324)
memory usage: 144.1+ MB
None


In [ ]:
mts_data.describe().transpose()

count          mean           std           min      25%      50%  \
[1:0]     7200.0  1.747670e+04  9.577068e+03 -2.759000e+04  11894.0  24121.0   
[1:1]     7200.0 -1.422589e+04  9.333231e+03 -3.212900e+04 -22435.0 -10137.0   
[1:2]     7200.0 -1.683807e+04  1.219468e+04 -3.121700e+04 -27227.0 -14957.0   
[1:3]     7200.0 -1.216929e+04  1.336145e+04 -3.231900e+04 -23672.0 -11379.0   
[1:4]     7097.0 -3.885881e+35  3.621291e+36 -4.253460e+37      0.0      0.0   
...          ...           ...           ...           ...      ...      ...   
[26.119]  7200.0  1.000000e+00  0.000000e+00  1.000000e+00      1.0      1.0   
[26.120]  7200.0  1.000000e+00  0.000000e+00  1.000000e+00      1.0      1.0   
[26.121]  7200.0  0.000000e+00  0.000000e+00  0.000000e+00      0.0      0.0   
[26.122]  7200.0  0.000000e+00  0.000000e+00  0.000000e+00      0.0      0.0   
[26.123]  7200.0  0.000000e+00  0.000000e+00  0.000000e+00      0.0      0.0   

              75%           max  
[1:0]     24121.0  2.996100e+04  
[1:1]    -10137.0  3.164900e+04  
[1:2]    -14957.0  3.227500e+04  
[1:3]    -11379.0  3.276500e+04  
[1:4]         0.0  1.623090e+32  
...           ...           ...  
[26.119]      1.0  1.000000e+00  
[26.120]      1.0  1.000000e+00  
[26.121]      0.0  0.000000e+00  
[26.122]      0.0  0.000000e+00  
[26.123]      0.0  0.000000e+00  

[2623 rows x 8 columns]

In [ ]:
# How many numbers of days data gathered
mts_data.index = pd.to_datetime(mts_data.index)
num_days_data_gathered = mts_data.index.max() - mts_data.index.min()
# Print the result
print("Number of days data was gathered:", num_days_data_gathered)

Number of days data was gathered: 0 days 01:59:59.030000


In [ ]:
# Count null values in each column
null_counts = mts_data.isnull().sum()
# Print the result
print(null_counts)

[1:0]         0
[1:1]         0
[1:2]         0
[1:3]         0
[1:4]       103
           ... 
[26.119]      0
[26.120]      0
[26.121]      0
[26.122]      0
[26.123]      0
Length: 2623, dtype: int64


In [ ]:
# Total number of rows
total_rows = len(mts_data)
# Percentage of null values in each column
null_percentages = (null_counts / total_rows) * 100
# Print the result
print(null_percentages)

[1:0]       0.000000
[1:1]       0.000000
[1:2]       0.000000
[1:3]       0.000000
[1:4]       1.430556
              ...   
[26.119]    0.000000
[26.120]    0.000000
[26.121]    0.000000
[26.122]    0.000000
[26.123]    0.000000
Length: 2623, dtype: float64


In [ ]:
null_counts = mts_data.isnull().sum()
print(null_counts)

[1:0]         0
[1:1]         0
[1:2]         0
[1:3]         0
[1:4]       103
           ... 
[26.119]      0
[26.120]      0
[26.121]      0
[26.122]      0
[26.123]      0
Length: 2623, dtype: int64


In [ ]:
total_null_values = null_counts.sum()
print(total_null_values)

1229


In [ ]:
mts_data

[1:0]  [1:1]  [1:2]  [1:3]  [1:4]         [1:5]  \
Time                                                                       
2023-11-12 07:58:28.430  24121 -10137 -14957 -11379    0.0  0.000000e+00   
2023-11-12 07:58:29.430  24121 -10137 -14957 -11379    0.0  0.000000e+00   
2023-11-12 07:58:30.430  24121 -10137 -14957 -11379    0.0  2.350990e-38   
2023-11-12 07:58:31.430  24121 -10137 -14957 -11379    0.0  0.000000e+00   
2023-11-12 07:58:32.430  24121 -10137 -14957 -11379    0.0  0.000000e+00   
...                        ...    ...    ...    ...    ...           ...   
2023-11-12 09:58:23.460  11894 -22435 -27227 -23672    0.0  0.000000e+00   
2023-11-12 09:58:24.460  11894 -22435 -27227 -23672    0.0  0.000000e+00   
2023-11-12 09:58:25.460  11894 -22435 -27227 -23672    0.0  0.000000e+00   
2023-11-12 09:58:26.460  11894 -22435 -27227 -23672    0.0           NaN   
2023-11-12 09:58:27.460  11894 -22435 -27227 -23672    0.0  0.000000e+00   

                         [1:6]  [1:7]  [1:8]  [1:9]  [1:10]  [1:11]  [1:12]  \
Time                                                                          
2023-11-12 07:58:28.430      0    330    330    332     332     900      90   
2023-11-12 07:58:29.430      0    330    330    332     332     900      90   
2023-11-12 07:58:30.430      1    330    330    332     332     900      90   
2023-11-12 07:58:31.430      0    330    330    332     332     900      90   
2023-11-12 07:58:32.430      0    330    330    332     332     900      90   
...                        ...    ...    ...    ...     ...     ...     ...   
2023-11-12 09:58:23.460      0     18     18     18      18    -900     -89   
2023-11-12 09:58:24.460      0     18     18     18      18    -900     -89   
2023-11-12 09:58:25.460      0     18     18     18      18    -900     -89   
2023-11-12 09:58:26.460     -1     18     18     18      18    -900     -89   
2023-11-12 09:58:27.460      0     18     18     18      18    -900     -89   

                         [1:13]  [1:14]  [1:15]  [1:16]  [1:17]  [1:18]  \
Time                                                                      
2023-11-12 07:58:28.430       0       0       0    1000       0       0   
2023-11-12 07:58:29.430       0       0       0    1000       0       0   
2023-11-12 07:58:30.430       0       0       0    1000       0       0   
2023-11-12 07:58:31.430       0       0       0    1000       0       0   
2023-11-12 07:58:32.430       0       0       0    1000       0       0   
...                         ...     ...     ...     ...     ...     ...   
2023-11-12 09:58:23.460       0       0       0    1000       0       0   
2023-11-12 09:58:24.460       0       0       0    1000       0       0   
2023-11-12 09:58:25.460       0       0       0    1000       0       0   
2023-11-12 09:58:26.460       0       0       0    1000       0       0   
2023-11-12 09:58:27.460       0       0       0    1000       0       0   

                         [1:19]  [1:20]  [1:21]  [1:22]  [1:23]  [1:24]  \
Time                                                                      
2023-11-12 07:58:28.430       0    1000     194       0       0       0   
2023-11-12 07:58:29.430       0    1000     194       0       0       0   
2023-11-12 07:58:30.430       0    1000     194       0       0       0   
2023-11-12 07:58:31.430       0    1000     194       0       0       0   
2023-11-12 07:58:32.430       0    1000     194       0       0       0   
...                         ...     ...     ...     ...     ...     ...   
2023-11-12 09:58:23.460       0    1000     125       0       0       0   
2023-11-12 09:58:24.460       0    1000     125       0       0       0   
2023-11-12 09:58:25.460       0    1000     125       0       0       0   
2023-11-12 09:58:26.460       0    1000     125       0       0       0   
2023-11-12 09:58:27.460       0    1000     125       0       0       0   

                         [1:25]  [1:26]  [1:27]  [1:28] 

In [ ]:
# Finding columns that have highest missing values percentage:
def highest_NAs_columns(df):
    # Calculate the number of missing values in each column and sort them in descending order of percentage
    nans = pd.DataFrame(mts_data.isnull().sum().sort_values(ascending=False) / len(mts_data), columns=['percent'])
    idx = nans['percent'] > 0
    return nans[idx]

top_missing_columns = highest_NAs_columns(mts_data).head(10)
print(top_missing_columns)

        percent
[1:5]  0.156389
[1:4]  0.014306


In [ ]:
mts_data['[1:5]']

Time
2023-11-12 07:58:28.430    0.000000e+00
2023-11-12 07:58:29.430    0.000000e+00
2023-11-12 07:58:30.430    2.350990e-38
2023-11-12 07:58:31.430    0.000000e+00
2023-11-12 07:58:32.430    0.000000e+00
                               ...     
2023-11-12 09:58:23.460    0.000000e+00
2023-11-12 09:58:24.460    0.000000e+00
2023-11-12 09:58:25.460    0.000000e+00
2023-11-12 09:58:26.460             NaN
2023-11-12 09:58:27.460    0.000000e+00
Name: [1:5], Length: 7200, dtype: float64

In [ ]:
mts_data['[1:4]']

Time
2023-11-12 07:58:28.430    0.0
2023-11-12 07:58:29.430    0.0
2023-11-12 07:58:30.430    0.0
2023-11-12 07:58:31.430    0.0
2023-11-12 07:58:32.430    0.0
                          ... 
2023-11-12 09:58:23.460    0.0
2023-11-12 09:58:24.460    0.0
2023-11-12 09:58:25.460    0.0
2023-11-12 09:58:26.460    0.0
2023-11-12 09:58:27.460    0.0
Name: [1:4], Length: 7200, dtype: float64

In [ ]:
mts_data

[1:0]  [1:1]  [1:2]  [1:3]  [1:4]         [1:5]  \
Time                                                                       
2023-11-12 07:58:28.430  24121 -10137 -14957 -11379    0.0  0.000000e+00   
2023-11-12 07:58:29.430  24121 -10137 -14957 -11379    0.0  0.000000e+00   
2023-11-12 07:58:30.430  24121 -10137 -14957 -11379    0.0  2.350990e-38   
2023-11-12 07:58:31.430  24121 -10137 -14957 -11379    0.0  0.000000e+00   
2023-11-12 07:58:32.430  24121 -10137 -14957 -11379    0.0  0.000000e+00   
...                        ...    ...    ...    ...    ...           ...   
2023-11-12 09:58:23.460  11894 -22435 -27227 -23672    0.0  0.000000e+00   
2023-11-12 09:58:24.460  11894 -22435 -27227 -23672    0.0  0.000000e+00   
2023-11-12 09:58:25.460  11894 -22435 -27227 -23672    0.0  0.000000e+00   
2023-11-12 09:58:26.460  11894 -22435 -27227 -23672    0.0           NaN   
2023-11-12 09:58:27.460  11894 -22435 -27227 -23672    0.0  0.000000e+00   

                         [1:6]  [1:7]  [1:8]  [1:9]  [1:10]  [1:11]  [1:12]  \
Time                                                                          
2023-11-12 07:58:28.430      0    330    330    332     332     900      90   
2023-11-12 07:58:29.430      0    330    330    332     332     900      90   
2023-11-12 07:58:30.430      1    330    330    332     332     900      90   
2023-11-12 07:58:31.430      0    330    330    332     332     900      90   
2023-11-12 07:58:32.430      0    330    330    332     332     900      90   
...                        ...    ...    ...    ...     ...     ...     ...   
2023-11-12 09:58:23.460      0     18     18     18      18    -900     -89   
2023-11-12 09:58:24.460      0     18     18     18      18    -900     -89   
2023-11-12 09:58:25.460      0     18     18     18      18    -900     -89   
2023-11-12 09:58:26.460     -1     18     18     18      18    -900     -89   
2023-11-12 09:58:27.460      0     18     18     18      18    -900     -89   

                         [1:13]  [1:14]  [1:15]  [1:16]  [1:17]  [1:18]  \
Time                                                                      
2023-11-12 07:58:28.430       0       0       0    1000       0       0   
2023-11-12 07:58:29.430       0       0       0    1000       0       0   
2023-11-12 07:58:30.430       0       0       0    1000       0       0   
2023-11-12 07:58:31.430       0       0       0    1000       0       0   
2023-11-12 07:58:32.430       0       0       0    1000       0       0   
...                         ...     ...     ...     ...     ...     ...   
2023-11-12 09:58:23.460       0       0       0    1000       0       0   
2023-11-12 09:58:24.460       0       0       0    1000       0       0   
2023-11-12 09:58:25.460       0       0       0    1000       0       0   
2023-11-12 09:58:26.460       0       0       0    1000       0       0   
2023-11-12 09:58:27.460       0       0       0    1000       0       0   

                         [1:19]  [1:20]  [1:21]  [1:22]  [1:23]  [1:24]  \
Time                                                                      
2023-11-12 07:58:28.430       0    1000     194       0       0       0   
2023-11-12 07:58:29.430       0    1000     194       0       0       0   
2023-11-12 07:58:30.430       0    1000     194       0       0       0   
2023-11-12 07:58:31.430       0    1000     194       0       0       0   
2023-11-12 07:58:32.430       0    1000     194       0       0       0   
...                         ...     ...     ...     ...     ...     ...   
2023-11-12 09:58:23.460       0    1000     125       0       0       0   
2023-11-12 09:58:24.460       0    1000     125       0       0       0   
2023-11-12 09:58:25.460       0    1000     125       0       0       0   
2023-11-12 09:58:26.460       0    1000     125       0       0       0   
2023-11-12 09:58:27.460       0    1000     125       0       0       0   

                         [1:25]  [1:26]  [1:27]  [1:28] 

**Data Normalization:**

In [ ]:
# Normalize the data
from sklearn.preprocessing import StandardScaler
scaler = StandardScaler()
mts_data_scaled = pd.DataFrame(scaler.fit_transform(mts_data), columns=mts_data.columns)

In [ ]:
mts_data_scaled

[1:0]     [1:1]     [1:2]     [1:3]     [1:4]     [1:5]     [1:6]  \
0     0.693820  0.438130  0.154264  0.059151  0.107314  0.196449  0.005371   
1     0.693820  0.438130  0.154264  0.059151  0.107314  0.196449  0.005371   
2     0.693820  0.438130  0.154264  0.059151  0.107314  0.196449  0.009787   
3     0.693820  0.438130  0.154264  0.059151  0.107314  0.196449  0.005371   
4     0.693820  0.438130  0.154264  0.059151  0.107314  0.196449  0.005371   
...        ...       ...       ...       ...       ...       ...       ...   
7195 -0.582964 -0.879618 -0.851982 -0.860948  0.107314  0.196449  0.005371   
7196 -0.582964 -0.879618 -0.851982 -0.860948  0.107314  0.196449  0.005371   
7197 -0.582964 -0.879618 -0.851982 -0.860948  0.107314  0.196449  0.005371   
7198 -0.582964 -0.879618 -0.851982 -0.860948  0.107314       NaN  0.000955   
7199 -0.582964 -0.879618 -0.851982 -0.860948  0.107314  0.196449  0.005371   

         [1:7]     [1:8]     [1:9]    [1:10]    [1:11]    [1:12]  [1:13]  \
0     0.981887  0.981887  0.981903  0.981893  1.048168  1.048091     0.0   
1     0.981887  0.981887  0.981903  0.981893  1.048168  1.048091     0.0   
2     0.981887  0.981887  0.981903  0.981893  1.048168  1.048091     0.0   
3     0.981887  0.981887  0.981903  0.981893  1.048168  1.048091     0.0   
4     0.981887  0.981887  0.981903  0.981893  1.048168  1.048091     0.0   
...        ...       ...       ...       ...       ...       ...     ...   
7195 -0.985165 -0.985165 -0.985373 -0.985373 -0.956693 -0.949300     0.0   
7196 -0.985165 -0.985165 -0.985373 -0.985373 -0.956693 -0.949300     0.0   
7197 -0.985165 -0.985165 -0.985373 -0.985373 -0.956693 -0.949300     0.0   
7198 -0.985165 -0.985165 -0.985373 -0.985373 -0.956693 -0.949300     0.0   
7199 -0.985165 -0.985165 -0.985373 -0.985373 -0.956693 -0.949300     0.0   

      [1:14]  [1:15]  [1:16]    [1:17]    [1:18]    [1:19]  [1:20]    [1:21]  \
0        0.0     0.0     0.0 -0.600708 -0.600712 -0.574108     0.0  0.358385   
1        0.0     0.0     0.0 -0.600708 -0.600712 -0.574108     0.0  0.358385   
2        0.0     0.0     0.0 -0.600708 -0.600712 -0.574108     0.0  0.358385   
3        0.0     0.0     0.0 -0.600708 -0.600712 -0.574108     0.0  0.358385   
4        0.0     0.0     0.0 -0.600708 -0.600712 -0.574108     0.0  0.358385   
...      ...     ...     ...       ...       ...       ...     ...       ...   
7195     0.0     0.0     0.0 -0.600708 -0.600712 -0.574108     0.0 -0.777916   
7196     0.0     0.0     0.0 -0.600708 -0.600712 -0.574108     0.0 -0.777916   
7197     0.0     0.0     0.0 -0.600708 -0.600712 -0.574108     0.0 -0.777916   
7198     0.0     0.0     0.0 -0.600708 -0.600712 -0.574108     0.0 -0.777916   
7199     0.0     0.0     0.0 -0.600708 -0.600712 -0.574108     0.0 -0.777916   

        [1:22]   [1:23]    [1:24]    [1:25]    [1:26]    [1:27]    [1:28]  \
0    -0.600867 -0.60094 -0.341804 -0.600925 -0.600927 -0.344703 -1.474316   
1    -0.600867 -0.60094 -0.341804 -0.600925 -0.600927 -0.344703 -1.442238   
2    -0.600867 -0.60094 -0.341804 -0.600925 -0.600927 -0.344703 -1.426199   
3    -0.600867 -0.60094 -0.341804 -0.600925 -0.600927 -0.344703 -1.410160   
4    -0.600867 -0.60094 -0.341804 -0.600925 -0.600927 -0.344703 -1.402141   
...        ...      ...       ...       ...       ...       ...       ...   
7195 -0.600867 -0.60094 -0.341804 -0.594621 -0.600927 -0.344703 -0.520000   
7196 -0.600867 -0.60094 -0.341804 -0.597773 -0.600927 -0.344703 -0.520000   
7197 -0.600867 -0.60094 -0.341804 -0.600925 -0.600927 -0.344703 -0.520000   
7198 -0.600867 -0.60094 -0.341804 -0.600925 -0.600927 -0.344703 -0.520000   
7199 -0.600867 -0.60094 -0.341804 -0.600925 -0.600927 -0.344703 -0.520000   

        [1:29]    [1:30]    [1:31]    [1:32]    [1:33]    [1:34]    [1:35]  \
0    -1.163339 -0.207409 -0.897925 -0.897931 -0.468096 -1.269685 -0.777671   
1    -1.003552 -0.207409 -0.897925 -0.897931 -0.468096 -1.269685 -0.777671   
2    -0.905221 -0.207409 -0.897925 -0.8

**Dataset Patitioning and Building and Visualizaing
Correlation Matrix and Correlation Graph:**

In [ ]:
# Define your GNN model for anomaly detection
class AnomalyDetectionGNN(nn.Module):
    def __init__(self, input_dim, hidden_dim, output_dim):
        super(AnomalyDetectionGNN, self).__init__()
        self.conv1 = GCNConv(input_dim, hidden_dim)
        self.conv2 = GCNConv(hidden_dim, output_dim)

    def forward(self, data):
        x, edge_index = data.x, data.edge_index
        x = F.relu(self.conv1(x, edge_index))
        x = F.relu(self.conv2(x, edge_index))
        return x

In [ ]:
window_size = 20
step_size = 10

In [ ]:
#  Define Sliding Intervals
def sliding_window(mts_data_scaled, window_size, step_size):
    for i in range(0, len(mts_data_scaled) - window_size + 1, step_size):
        yield mts_data_scaled[i:i+window_size]

In [ ]:
#  Calculate Correlation Coefficients
def calculate_correlation_matrix(window_data, method='pearson'):
    correlation_matrix = window_data.corr(method=method)
    return correlation_matrix

In [ ]:
#  Construct Correlation Graph
def construct_correlation_graph(correlation_matrix):
    edge_index = []
    edge_attr = []

    for i, col1 in enumerate(correlation_matrix.columns):
        for j, col2 in enumerate(correlation_matrix.columns):
            if i < j:
                correlation = correlation_matrix.iloc[i, j]
                edge_index.append([i, j])
                edge_attr.append(correlation)

    edge_index = torch.tensor(edge_index).t().contiguous()
    edge_attr = torch.tensor(edge_attr)

    data = Data(edge_index=edge_index, edge_attr=edge_attr)
    return data

In [ ]:
# Constructing Correlation Graphs
correlation_graphs = []

# Generate sliding intervals and calculate correlation graphs
for window_data in sliding_window(mts_data_scaled, window_size, step_size):
    correlation_matrix = calculate_correlation_matrix(window_data)
    correlation_graph = construct_correlation_graph(correlation_matrix)
    correlation_graphs.append(correlation_graph)

# Plot the first correlation graph (for demonstration)
plt.figure(figsize=(8, 6))
plt.title('Correlation Graph for the First Sliding Interval')
plt.scatter(correlation_graphs[0].edge_index[0], correlation_graphs[0].edge_index[1], c=correlation_graphs[0].edge_attr, cmap='viridis')
plt.colorbar(label='Correlation Coefficient')
plt.xlabel('Node Index')
plt.ylabel('Node Index')
plt.grid(True)
plt.show()